In [ ]:
import time
import json
import datetime

from scipy.optimize import minimize
from scipy.sparse import lil_matrix
import numpy as np
import pandas as pd

# Display all rows.
pd.set_option('display.max_rows', None)

from plot import plot_results
from setup import *

## Bounds

In [ ]:
bounds = [[INPUT_FLOW_MIN, INPUT_FLOW_MAX]] * time_steps + [[OUTPUT_FLOW_MIN, OUTPUT_FLOW_MAX]] * time_steps

## Constraints

In [ ]:
def calculate_tank_levels(iflow, oflow):
    """Find tank level for each time step by cumumlative sum of inflow and out
    """
    return CAPACITY_INITIAL + np.cumsum(dt * (iflow - oflow))

In [ ]:
def tank_constraint(x):
    """Constraint on tank capacity.
    
    Will return a negative value if the tank either overflows or underflows.

    Since these two conditions are mutually exclusive we can combine this into a single constraint.
    """
    iflow = x[:time_steps]
    oflow = x[time_steps:]
    
    levels = calculate_tank_levels(iflow, oflow)
    
    return np.minimum(tank.capacity - levels, levels)

In [ ]:
constraints = [
    {"type": "ineq", "fun": tank_constraint},
]

## Optimisation

In [ ]:
def objective(x):
    iflow = x[:time_steps]
    oflow = x[time_steps:]

    ismooth = np.sum(np.abs(iflow[1:] - iflow[:-1]))
    osmooth = np.sum(np.abs(oflow[1:] - oflow[:-1]))
    difference = np.sum(np.abs(oflow - DEMAND))

    return difference + 0.1 * ismooth + 0.1 * osmooth

In [ ]:
def jacobian(x):
    iflow = x[:time_steps]
    oflow = x[time_steps:]
    grad = np.zeros_like(x)
    
    grad[1:time_steps] += 0.1 * np.sign(iflow[1:] - iflow[:-1])
    grad[:time_steps-1] -= 0.1 * np.sign(iflow[1:] - iflow[:-1])

    grad[time_steps+1:] += 0.1 * np.sign(oflow[1:] - oflow[:-1])
    grad[time_steps:-1] -= 0.1 * np.sign(oflow[1:] - oflow[:-1])
    
    grad[time_steps:] += np.sign(oflow - DEMAND)
    
    return grad

In [ ]:
# Initial guesses.
x0 = np.concatenate([
    # Inflow.
    np.full(time_steps, INPUT_FLOW_MIN, dtype=float),
    # Outflow.
    np.full(time_steps, OUTPUT_FLOW_MIN, dtype=float),
])

In [ ]:
# SOLVER = 'COBYQA'
# extra_options = {
#     'maxiter': 1000,
# }

# SOLVER = 'COBYLA'
# extra_options = {
#     'maxiter': 1000,
# }

# SOLVER = "trust-constr"
# extra_options = {
#     'maxiter': 10000,
#     "verbose": 2
# }

SOLVER = 'SLSQP'
extra_options = {
    'maxiter': 1000,
}

In [ ]:
start = time.perf_counter()
#
result = minimize(
    objective,
    x0,
    jac=jacobian,
    bounds=bounds,
    constraints=constraints,
    options={
        'disp': True,
        **extra_options
    },
    method=SOLVER,
)
#
end = time.perf_counter()

In [ ]:
iflow = result.x[:time_steps]
oflow = result.x[time_steps:]

results = pd.DataFrame({
    "time": TIMES,
    "demand": DEMAND,
    "inflow": iflow,
    "outflow": oflow,
    "level": calculate_tank_levels(iflow, oflow),
})

plt = plot_results(results)

plt.savefig(f"tank-global-scipy-solution-{str(SOLVER).lower()}.png", format="png", dpi=300)

plt.show()

In [ ]:
with open(f"tank-global-scipy-solution-{str(SOLVER).lower()}.json", "w") as f:
    json.dump(
        {
            "objective": round(result.fun, 3),
            "time": round(end - start, 3),
            "timestamp": datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S"),
        },
        f, indent=4
    )